In [64]:
import tushare as ts
import matplotlib.pyplot as plt
import pandas as pd
import MySQLdb
import time
import datetime
import warnings
warnings.filterwarnings("ignore")
from imp import reload
import chan

In [113]:
df=pd.DataFrame(columns=['ts_code','trade_time','trade_date','high','low','open','close'])
ts_code_list=[]
trade_time_list=[]
trade_date_list=[]
high_list=[]
low_list=[]
open_list=[]
close_list=[]
base_time=datetime.datetime.now()
v=20
for i in range(600000):
    rd=random.randint(0,20)-10
    ts_code='000000.SZ'
    time_time=base_time+datetime.timedelta(minutes=i-600000)
    trade_time=time_time.strftime("%Y-%m-%d %H:%M:%S")
    trade_date=time_time.strftime("%Y-%m-%d")
    high=v if rd<=0 else v+rd
    low=v if rd>0 else v-rd
    open=v
    close=v+rd
    ts_code_list.append(ts_code)
    trade_time_list.append(trade_time)
    trade_date_list.append(trade_date)
    high_list.append(high)
    low_list.append(low)
    open_list.append(open)
    close_list.append(close)
    v=v+rd
df = pd.DataFrame({'ts_code':ts_code_list, 'trade_time':trade_time_list, 'trade_date':trade_date_list, 'high':high_list, 'low':low_list, 'open':open_list, 'close':close_list})
print('build end')
reload(chan) #重新加载外部chan.py
df=chan.build(df)
print('handle end')

build end
handle end


In [100]:
ts_code_list

['000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '000000.SZ',
 '0000

In [114]:
result_df=pd.DataFrame()
found_qs_count=0 #找到的趋势数
found_count=0 #符合趋势的本组中枢已找到个数
zs_no_pre=0
zs_zg_pre=0
zs_zd_pre=0    
zs_gg_pre=0
zs_dd_pre=0
zs_direction_pre=''
for n, k in df.loc[(df["line"]=='bottom') | (df["line"]=='top')].iterrows():
    #print(k.zs_no, n, zs_no_pre==0 , k.zs_no>zs_no_pre)
    if k.zs_no!=0 and (zs_no_pre==0 or k.zs_no>zs_no_pre): #新中枢
        #print(k.zs_no,"新中枢",k.zs_no,k.zs_direction)
        if found_count==0 and (k.zs_direction=='downdown' or k.zs_direction=='upup'):
            found_count=found_count+1
        else: #前面已经找到一个待确认的
            if zs_direction_pre=='downdown' and k.zs_direction=='downdown' and k.gg<zs_dd_pre: #与前面的方向一致
                found_count=found_count+1
                #print('下降趋势延申')
            elif zs_direction_pre=='upup' and k.zs_direction=='upup' and k.dd>zs_gg_pre: #与前面的方向一致
                found_count=found_count+1
                #print('上升趋势延申')
            elif k.zs_direction=='upup' or k.zs_direction=='downdown': #盘整中枢，结束
                found_count=0
                #print('×盘整中枢，重新找')
            elif zs_direction_pre!=k.zs_direction: #与前面的方向不一致，作为第一个继续往下找
                found_count=1
                #print('×与之前方向不同，作为第一个往下找')
            else: #不成趋势
                found_count=1
                #print('×条件不符合，作为第一个往下找')
            if found_count>=2: #找到两个，记录
                found_qs_count=found_qs_count+1
                result_df=result_df.append({'ts_code':k.ts_code, 'trade_time':k.zs_confirm_time, 'trade_price':k.zs_confirm_price, 'n':n, 'direction': k.zs_direction},ignore_index=True)
                print('√找到两个连续符合中枢',k.ts_code, k.zs_confirm_time, k.zs_no,'共找到：',found_qs_count)
                found_count=0
        zs_no_pre=k.zs_no
        zs_zg_pre=k.zg
        zs_zd_pre=k.zg    
        zs_gg_pre=k.gg
        zs_dd_pre=k.dd
        zs_direction_pre=k.zs_direction
    elif k.zs_no==0 and found_count>0:
        line_point=k.high if k.line=='top' else k.low
        if (zs_direction_pre=='upup' and line_point<zs_gg_pre) or (zs_direction_pre=='downdown' and line_point>zs_dd_pre): #连接线段触碰前中枢
            found_count=0
            #print('×连接不符合')

√找到两个连续符合中枢 000000.SZ 2018-09-24 15:52:55 4 共找到： 1
√找到两个连续符合中枢 000000.SZ 2018-09-29 07:53:55 16 共找到： 2
√找到两个连续符合中枢 000000.SZ 2018-10-15 04:53:55 51 共找到： 3
√找到两个连续符合中枢 000000.SZ 2018-10-24 09:02:55 72 共找到： 4
√找到两个连续符合中枢 000000.SZ 2018-10-25 18:09:55 76 共找到： 5
√找到两个连续符合中枢 000000.SZ 2018-11-01 17:43:55 93 共找到： 6
√找到两个连续符合中枢 000000.SZ 2018-11-03 11:22:55 97 共找到： 7
√找到两个连续符合中枢 000000.SZ 2018-11-21 13:33:55 136 共找到： 8
√找到两个连续符合中枢 000000.SZ 2018-12-07 00:30:55 168 共找到： 9
√找到两个连续符合中枢 000000.SZ 2018-12-10 12:08:55 180 共找到： 10
√找到两个连续符合中枢 000000.SZ 2018-12-17 22:11:55 193 共找到： 11
√找到两个连续符合中枢 000000.SZ 2018-12-22 04:05:55 203 共找到： 12
√找到两个连续符合中枢 000000.SZ 2018-12-30 14:09:55 225 共找到： 13
√找到两个连续符合中枢 000000.SZ 2019-01-10 17:23:55 251 共找到： 14
√找到两个连续符合中枢 000000.SZ 2019-01-21 10:51:55 274 共找到： 15
√找到两个连续符合中枢 000000.SZ 2019-01-29 03:49:55 294 共找到： 16
√找到两个连续符合中枢 000000.SZ 2019-02-24 09:41:55 359 共找到： 17
√找到两个连续符合中枢 000000.SZ 2019-02-27 07:56:55 366 共找到： 18
√找到两个连续符合中枢 000000.SZ 2019-03-03 22:57:55 373

In [115]:
result_df.groupby('direction')['trade_price'].mean()

direction
downdown   -1461.333333
upup        -783.840000
Name: trade_price, dtype: float64

In [112]:
result_df

direction         n  trade_price           trade_time    ts_code
0       upup   45429.0       1290.0  2018-10-23 08:21:12  000000.SZ
1       upup   48185.0       1407.0  2018-10-25 07:29:12  000000.SZ
2   downdown   51333.0        929.0  2018-10-27 23:29:12  000000.SZ
3   downdown   53204.0        629.0  2018-10-29 00:41:12  000000.SZ
4   downdown   54092.0        470.0  2018-10-29 09:50:12  000000.SZ
5   downdown   54601.0        214.0  2018-10-29 22:19:12  000000.SZ
6   downdown   58285.0       -421.0  2018-11-01 10:22:12  000000.SZ
7       upup   63365.0        472.0  2018-11-04 23:05:12  000000.SZ
8       upup   64607.0        817.0  2018-11-05 20:53:12  000000.SZ
9   downdown   66698.0        184.0  2018-11-07 09:26:12  000000.SZ
10      upup   70424.0        400.0  2018-11-09 21:17:12  000000.SZ
11      upup   76868.0       1034.0  2018-11-14 10:30:12  000000.SZ
12      upup   82272.0       1133.0  2018-11-18 11:25:12  000000.SZ
13      upup   84398.0       1476.0  2018-11-19 11:40:12  000000.SZ
14      upup  100205.0       1383.0  2018-11-30 11:21:12  000000.SZ
15      upup  105761.0       2088.0  2018-12-04 09:59:12  000000.SZ
16  downdown  113752.0       1378.0  2018-12-10 00:32:12  000000.SZ
17  downdown  170353.0       1172.0  2019-01-18 03:43:12  000000.SZ
18      upup  174766.0       1300.0  2019-01-21 05:57:12  000000.SZ
19      upup  175605.0       1606.0  2019-01-22 10:34:12  000000.SZ
20      upup  183268.0       2016.0  2019-01-27 05:57:12  000000.SZ
21      upup  192731.0       2224.0  2019-02-02 18:27:12  000000.SZ
22      upup  257518.0          6.0  2019-03-19 18:26:12  000000.SZ
23      upup  273238.0       2494.0  2019-03-30 19:52:12  000000.SZ
24      upup  290749.0       2474.0  2019-04-11 21:15:12  000000.SZ
25      upup  295643.0       2766.0  2019-04-15 05:07:12  000000.SZ
26      upup  296349.0       3052.0  2019-04-15 19:37:12  000000.SZ
27  downdown  333239.0       4771.0  2019-05-11 08:41:12  000000.SZ
28  downdown  341253.0       5130.0  2019-05-17 00:20:12  000000.SZ
29      upup  399803.0       3068.0  2019-06-26 15:12:12  000000.SZ
30  downdown  413327.0       2339.0  2019-07-06 03:03:12  000000.SZ
31      upup  429276.0       1670.0  2019-07-17 00:40:12  000000.SZ
32      upup  431950.0       2285.0  2019-07-18 20:08:12  000000.SZ
33      upup  440072.0       1691.0  2019-07-24 18:03:12  000000.SZ
34  downdown  443888.0       1244.0  2019-07-27 09:26:12  000000.SZ
35  downdown  467004.0        457.0  2019-08-12 09:48:12  000000.SZ
36      upup  484840.0       -161.0  2019-08-24 22:35:12  000000.SZ
37  downdown  497936.0        285.0  2019-09-03 00:26:12  000000.SZ
38  downdown  501125.0       -401.0  2019-09-05 01:05:12  000000.SZ
39  downdown  502218.0       -679.0  2019-09-06 07:36:12  000000.SZ
40  downdown  517298.0      -1184.0  2019-09-16 03:25:12  000000.SZ
41      upup  518586.0       -825.0  2019-09-17 03:41:12  000000.SZ
42  downdown  571627.0       -670.0  2019-10-24 03:29:12  000000.SZ
43  downdown  596568.0      -1453.0  2019-11-10 12:18:12  000000.SZ